Importing Libraries

In [1]:
import re
import io
import csv
import nltk
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from nltk.tokenize import word_tokenize

Read CSV data

In [2]:
data = pd.read_csv("Sinhala_Singlish_Hate_Speech.csv")

In [3]:
data.head()

PhraseNo                                             Phrase IsHateSpeech
0         1  මේ බැල්ලි කොටින්ගේ ගු කනකොට අපහසුවක් දැනුනෙ නැ...          YES
1         2  මන් ඊයේ මුස්ලිම් ඩෑල් එකක් එක්ක සෙල්ෆියක් ගත්ත...          YES
2         3                           සංහිදියාවට අවුලක් වෙයි ද           NO
3         4  .කටින් පුරසාරම් දොඩන අපි සිංහලයො විදියට ලැජ්ජා...          YES
4         5  මචන් ඔය මගුල නවත්තලා කොන්දක් තියෙනවානම් පුලුවන...          YES

Data cleaning

In [4]:
def preporocessingText(sentence):
    cleaner_htmlTags  = re.compile('<.*?>|&([a-z0-9]+|#[0-9]{1,6}|#x[0-9a-f]{1,6});')
    cleantext_htmltags = re.sub(cleaner_htmlTags, '',sentence).lower()
    cleantext_NonAlp = re.compile(u'[^\u0061-\u007A|^\u0D80-\u0DFF|^\u0030-\u0039]', re.UNICODE)
    cleantext_finalText = re.sub(cleantext_NonAlp, ' ',cleantext_htmltags).strip(" ")
    return cleantext_finalText

Check whether sentences have full english letters or mix of english & sinhala words

In [5]:
def isSinglish(sentence):
    try:
        sentence.encode(encoding='utf-8').decode('ascii')
    except UnicodeDecodeError:
        return False
    else:
        return True

Generate three separate dataframes

In [6]:
df_Sinhala  = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])
df_Singlish = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])
df_All_preprocess = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])


singish_index = 1
sinhala_index = 1

for i in range(data.shape[0]):
    dataSentence = data['Phrase'][i]
    preprocessData = preporocessingText(dataSentence)

    if(isSinglish(dataSentence)):
        df_Singlish.loc[singish_index-1] = [singish_index] + [preprocessData] + [data['IsHateSpeech'][i]]
        singish_index += 1

    else:
        df_Sinhala.loc[sinhala_index-1] = [sinhala_index] + [preprocessData] + [data['IsHateSpeech'][i]]
        sinhala_index += 1
        
    df_All_preprocess.loc[i] = [i+1] + [preprocessData] + [data['IsHateSpeech'][i]]

In [7]:
df_Sinhala.head()

PhraseNo                                             Phrase IsHateSpeech
0         1  මේ බැල්ලි කොටින්ගේ ගු කනකොට අපහසුවක් දැනුනෙ නැ...          YES
1         2  මන් ඊයේ මුස්ලිම් ඩෑල් එකක් එක්ක සෙල්ෆියක් ගත්ත...          YES
2         3                           සංහිදියාවට අවුලක් වෙයි ද           NO
3         4  කටින් පුරසාරම් දොඩන අපි සිංහලයො විදියට ලැජ්ජා ...          YES
4         5  මචන් ඔය මගුල නවත්තලා කොන්දක් තියෙනවානම් පුලුවන...          YES

In [8]:
df_Singlish.head()

PhraseNo                                             Phrase IsHateSpeech
0         1  menna ratawal menna minissu  ape ratawal wala ...          YES
1         2  paduway hitahan beri weda nokaran bat eka gath...          YES
2         3  muth kata arinne anik unta witharai jathiyata ...          YES
3         4  songs kanna epa buruwo kochchara lassana sindu...          YES
4         5  muth nanna yanne kridakayanta ground walata we...          YES

Print percentage of the data

In [9]:
sinhala_sent_percentage = (sinhala_index/data.shape[0])*100
singlish_sent_percentage = (singish_index/data.shape[0])*100
print("Sinhala sentences percentage(mix sinhala and english letters)  = ",str(sinhala_sent_percentage)+" %")
print("Singlish sentences percentage(only has english letters) = ",str(singlish_sent_percentage) +" %")

Sinhala sentences percentage(mix sinhala and english letters)  =  72.48 %
Singlish sentences percentage(only has english letters) =  27.6 %


In [10]:
def getUniqueTokens(myarr):
    myset = list(set(myarr))
    return myset

def joinWordsIntoSentence(dataframe):
    for itm in range(len(dataframe)):
        words_arr = dataframe['Phrase'][itm]
        dataframe['Phrase'][itm] = ( " ".join( words_arr ))

### Sinhala Only Dataset (has Sinhala and English words)

#### Sinhala stop words removal

In [11]:
f_stopWords = io.open("Stopwords.txt", mode="r", encoding="utf-16")
sinhala_stop_words = []
df_StopWordsRemoval_Sinhala = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])

for x in f_stopWords:
  sinhala_stop_words.append(x.split()[0])

In [12]:
nltk.download('punkt')

SinhalaData = df_Sinhala
prev_lengths_arr = []
prev_lengths_arr_unique = []
after_removal_stopWords_lenghts_arr = []
after_removal_stopWords_lenghts_arr_unique = []

for k in range(SinhalaData.shape[0]):
    SentenceTokens = word_tokenize(SinhalaData['Phrase'][k])

    prev_lengths_arr.append(len(SentenceTokens))
    prev_lengths_arr_unique.append(len(getUniqueTokens(SentenceTokens)))
    removing_stopwords_sentence = [word for word in SentenceTokens if word not in sinhala_stop_words]
    after_removal_stopWords_lenghts_arr.append(len(removing_stopwords_sentence))
    after_removal_stopWords_lenghts_arr_unique.append(len(getUniqueTokens(removing_stopwords_sentence)))
    df_StopWordsRemoval_Sinhala.loc[k] = [k+1] + [removing_stopwords_sentence] + [SinhalaData['IsHateSpeech'][k]]

joinWordsIntoSentence(df_StopWordsRemoval_Sinhala )

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\kanis\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a Da

In [13]:
df_StopWordsRemoval_Sinhala

PhraseNo                                             Phrase IsHateSpeech
0            1  බැල්ලි කොටින්ගේ ගු කනකොට අපහසුවක් දැනුනෙ දන් ඔ...          YES
1            2  මන් ඊයේ මුස්ලිම් ඩෑල් එකක් සෙල්ෆියක් ගත්තා සහජ...          YES
2            3                             සංහිදියාවට අවුලක් වෙයි           NO
3            4  කටින් පුරසාරම් දොඩන අපි සිංහලයො විදියට ලැජ්ජා ...          YES
4            5  මචන් මගුල නවත්තලා කොන්දක් තියෙනවානම් පුලුවන්නම...          YES
...        ...                                                ...          ...
1806      1807  දෙන්නා එකතු වෙලා tv program එකක් කරන්නකො තියන ...           NO
1807      1808  මොනා කිව්වත් ඔයාල දෙන්නගෙ කටවල් දෙකට ගහන්න ලංක...           NO
1808      1809  ඇස්වහ කටවහක් ඔයාලා දෙනාටම හැමදාමත් අපිව සතුටින...           NO
1809      1810  මුන් දෙන්න රෙඩියෝ එකේ සුපිරි ඩබල හිරු ඉන්න කාල...           NO
1810      1811  ane manda joke eka hodai eth wadu දෙමව්පියන්ව ...           NO

[1811 rows x 3 columns]

#### Sinhala stemming

In [14]:
f_suffixes = io.open("Suffixes.txt", mode="r", encoding="utf-16")
sinhala_suffixes = []
df_Stemming_Sinhala = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])
afterStemingLenghtsUnique = []

for suf in f_suffixes:
  sinhala_suffixes.append(suf.strip().split()[0])

In [15]:
def isSuffix(s1, s2):

    n1 = len(s1)
    n2 = len(s2)
    if (n1 > n2):
        return False
    for i in range(n1):
        if(s1[n1 - i - 1] != s2[n2 - i - 1]):
            return False
    return True

def removeSuffix(word,suffix):
    newLen = len(word)-len(suffix)
    wordN = word[0:newLen]
    return wordN

In [16]:
def stemming(data_frame):
    stems = {}
    found = 0
    df_Stemming = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])
    for r in range(data_frame.shape[0]):
        Sentence = data_frame['Phrase'][r]
        SentenceTokens = word_tokenize(Sentence)
        stemming_sentence_n = []
        for wr in SentenceTokens:
            found = 0
            for suf in sinhala_suffixes:
                if(isSuffix(suf.strip(),wr.strip())):
                    stm = removeSuffix(wr.strip(),suf.strip())
                    stems[wr] = stm
                    stemming_sentence_n.append(stems[wr])
                    found = 1
                    break

            if(found == 0):
                stemming_sentence_n.append(wr)

        df_Stemming.loc[r] = [r+1] + [stemming_sentence_n] + [data_frame['IsHateSpeech'][r]]
        stemming_sentence_n = []
    print(stems)
    joinWordsIntoSentence(df_Stemming)
    return df_Stemming

In [17]:
df_Stemming_Sinhala = stemming(df_StopWordsRemoval_Sinhala)

{'කොටින්ගේ': 'කොටින්', 'ගු': 'ග', 'කනකොට': 'කනකො', 'අපහසුවක්': 'අපහසුවක', 'දැනුනෙ': 'දැනුන', 'දන්': 'දන', 'ඔකිට': 'ඔ', 'මිනිහා': 'මිනිහ', 'මැරුනම': 'මැරුන', 'දැනුන': 'දැනු', 'දුකට': 'දු', 'දහස්': 'දහස', 'ගුනයක': 'ගුනය', 'දුකක්': 'දුකක', 'දැනෙනවා': 'දැනෙ', 'ඉස්සරහට': 'ඉස්සරහ', 'උපසම්පදාව': 'උපසම්පදා', 'තියන': 'තිය', 'භික්සුවක්': 'භික්සුවක', 'හිරේ': 'හිර', 'යැවුවට': 'යැවුව', 'ඔකි': 'ඔ', 'වැඩියෙන්ම': 'වැඩියෙන්', 'ආදරේ': 'ආදර', 'කෙනෙක්': 'කෙනෙක', 'නැති': 'නැ', 'වෙනවා': 'වෙ', 'කල්': 'කල', 'නොගිහින්': 'නොගිහින', 'මන්': 'මන', 'ඊයේ': 'ඊ', 'මුස්ලිම්': 'මුස්ලිම', 'ඩෑල්': 'ඩෑල', 'එකක්': 'එකක', 'සෙල්ෆියක්': 'සෙල්ෆියක', 'ගත්තා': 'ගත්ත', 'සහජීවනේ': 'සහජීවන', 'රැකගෙන': 'රැකගෙ', 'යන්න': 'යන්', 'ඒක': 'ඒ', 'තාම': 'තා', 'දාලා': 'දා', 'පරයා': 'පර', 'සංහිදියාවට': 'සංහිදියාව', 'අවුලක්': 'අවුලක', 'වෙයි': 'වෙ', 'කටින්': 'කටින', 'පුරසාරම්': 'පුරසාරම', 'දොඩන': 'දොඩ', 'සිංහලයො': 'සිංහලය', 'විදියට': 'විදිය', 'ලැජ්ජා': 'ලැජ්ජ', 'විය': 'වි', 'යුතුයි': 'යුතු', 'මචන්': 'මචන', 'මගුල': 'මගු', 'නවත්තලා': 'නවත්ත', 'කොන්ද

C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  da

In [18]:
df_Stemming_Sinhala

PhraseNo                                             Phrase IsHateSpeech
0            1  බැල්ලි කොටින් ග කනකො අපහසුවක දැනුන දන ඔ මිනිහ ...          YES
1            2  මන ඊ මුස්ලිම ඩෑල එකක සෙල්ෆියක ගත්ත සහජීවන රැකග...          YES
2            3                                 සංහිදියාව අවුලක වෙ           NO
3            4    කටින පුරසාරම දොඩ අපි සිංහලය විදිය ලැජ්ජ වි යුතු          YES
4            5  මචන මගු නවත්ත කොන්දක තියෙනවානම පුලුවන්නම කර පෙ...          YES
...        ...                                                ...          ...
1806      1807  දෙන් එකත වෙ tv program එකක කරන්නක තිය talent ඒ...           NO
1807      1808      මො කිව්වත ඔයා දෙන්න කටවල දෙ ගහන් ලංකා කටක පට්           NO
1808      1809  ඇස්වහ කටවහක ඔයා දෙනා හැමදාමත අපි සතුටින තියන් ...           NO
1809      1810  මුන දෙන් රෙඩි එ සුපිරි ඩබ හිර ඉන් කාල ඉදන අහ d...           NO
1810      1811  ane manda joke eka hodai eth wadu දෙමව්පියන් ව...           NO

[1811 rows x 3 columns]

In [19]:
df_Stemming_Sinhala.to_csv('sinhala_preprocessed/sinhala_preprocessed.csv', index=False)

### Singlish Only Dataset (Only include English letters)

no need to do the stopewords removal and stemming since there are no any methods have been founds for these words

In [20]:
SinglishData = df_Singlish

In [21]:
df_Singlish_unique = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])
prev_lengths_arr_singlish = []
after_unique_arr_singlish = []

for r in range(SinglishData.shape[0]):
     Sentence_singlish = word_tokenize(SinglishData['Phrase'][r])
     prev_lengths_arr_singlish.append(len(Sentence_singlish))
     unique_sentence = getUniqueTokens(Sentence_singlish)
     df_Singlish_unique.loc[r] = [r+1] + [unique_sentence] + [SinglishData['IsHateSpeech'][r]]

     after_unique_arr_singlish.append(len(unique_sentence))

joinWordsIntoSentence(df_Singlish_unique)

C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  da

In [22]:
df_Singlish_unique.to_csv('singlish_preprocessed/singlish_preprocessed.csv', index=False)

### Combined Dataset (Both Sinhala & English Sentences)

Stopwords removal

In [23]:
df_StopWordsRemoval_All = pd.DataFrame(columns=['PhraseNo', 'Phrase', 'IsHateSpeech'])
pre_len_arr_all = []
AllData = df_All_preprocess

for k in range(AllData.shape[0]):
    SentenceTokens = word_tokenize(AllData['Phrase'][k])
    pre_len_arr_all.append(len(SentenceTokens))
    removing_stopwords_sentence_all = [word for word in SentenceTokens if word not in sinhala_stop_words]
    df_StopWordsRemoval_All.loc[k] = [k+1] + [removing_stopwords_sentence_all] + [AllData['IsHateSpeech'][k]]

joinWordsIntoSentence(df_StopWordsRemoval_All)

C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  da

In [24]:
df_StopWordsRemoval_All

PhraseNo                                             Phrase IsHateSpeech
0            1  බැල්ලි කොටින්ගේ ගු කනකොට අපහසුවක් දැනුනෙ දන් ඔ...          YES
1            2  මන් ඊයේ මුස්ලිම් ඩෑල් එකක් සෙල්ෆියක් ගත්තා සහජ...          YES
2            3                             සංහිදියාවට අවුලක් වෙයි           NO
3            4  කටින් පුරසාරම් දොඩන අපි සිංහලයො විදියට ලැජ්ජා ...          YES
4            5  මචන් මගුල නවත්තලා කොන්දක් තියෙනවානම් පුලුවන්නම...          YES
...        ...                                                ...          ...
2495      2496  දෙන්නා එකතු වෙලා tv program එකක් කරන්නකො තියන ...           NO
2496      2497  මොනා කිව්වත් ඔයාල දෙන්නගෙ කටවල් දෙකට ගහන්න ලංක...           NO
2497      2498  ඇස්වහ කටවහක් ඔයාලා දෙනාටම හැමදාමත් අපිව සතුටින...           NO
2498      2499  මුන් දෙන්න රෙඩියෝ එකේ සුපිරි ඩබල හිරු ඉන්න කාල...           NO
2499      2500  ane manda joke eka hodai eth wadu දෙමව්පියන්ව ...           NO

[2500 rows x 3 columns]

stemming

In [25]:
df_Stemming_All = stemming(df_StopWordsRemoval_All)

{'කොටින්ගේ': 'කොටින්', 'ගු': 'ග', 'කනකොට': 'කනකො', 'අපහසුවක්': 'අපහසුවක', 'දැනුනෙ': 'දැනුන', 'දන්': 'දන', 'ඔකිට': 'ඔ', 'මිනිහා': 'මිනිහ', 'මැරුනම': 'මැරුන', 'දැනුන': 'දැනු', 'දුකට': 'දු', 'දහස්': 'දහස', 'ගුනයක': 'ගුනය', 'දුකක්': 'දුකක', 'දැනෙනවා': 'දැනෙ', 'ඉස්සරහට': 'ඉස්සරහ', 'උපසම්පදාව': 'උපසම්පදා', 'තියන': 'තිය', 'භික්සුවක්': 'භික්සුවක', 'හිරේ': 'හිර', 'යැවුවට': 'යැවුව', 'ඔකි': 'ඔ', 'වැඩියෙන්ම': 'වැඩියෙන්', 'ආදරේ': 'ආදර', 'කෙනෙක්': 'කෙනෙක', 'නැති': 'නැ', 'වෙනවා': 'වෙ', 'කල්': 'කල', 'නොගිහින්': 'නොගිහින', 'මන්': 'මන', 'ඊයේ': 'ඊ', 'මුස්ලිම්': 'මුස්ලිම', 'ඩෑල්': 'ඩෑල', 'එකක්': 'එකක', 'සෙල්ෆියක්': 'සෙල්ෆියක', 'ගත්තා': 'ගත්ත', 'සහජීවනේ': 'සහජීවන', 'රැකගෙන': 'රැකගෙ', 'යන්න': 'යන්', 'ඒක': 'ඒ', 'තාම': 'තා', 'දාලා': 'දා', 'පරයා': 'පර', 'සංහිදියාවට': 'සංහිදියාව', 'අවුලක්': 'අවුලක', 'වෙයි': 'වෙ', 'කටින්': 'කටින', 'පුරසාරම්': 'පුරසාරම', 'දොඩන': 'දොඩ', 'සිංහලයො': 'සිංහලය', 'විදියට': 'විදිය', 'ලැජ්ජා': 'ලැජ්ජ', 'විය': 'වි', 'යුතුයි': 'යුතු', 'මචන්': 'මචන', 'මගුල': 'මගු', 'නවත්තලා': 'නවත්ත', 'කොන්ද

C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  dataframe['Phrase'][itm] = ( " ".join( words_arr ))
C:\Users\kanis\AppData\Local\Temp\ipykernel_5024\828503734.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  da

In [26]:
df_Stemming_All.to_csv('combined_preprocessed/combined_preprocessed.csv', index=False)